# Regular Expressions for Data Cleaning in Python
This tutorial introduces regular expressions (regex) for data cleaning.

In [ ]:
from datascience import *
import re

In [ ]:
text = "Once upon a midnight dreary, while I pondered, weak and weary, \
Over many a quaint and curious volume of forgotten lore— \
    While I nodded, nearly napping, suddenly there came a tapping, "
text2 = "That costs $59.76.  Thank you."

# Regex Basics - Metacharacters

In [ ]:
re.findall("napping", text)

In [ ]:
# [] - A set of characters, e.g. [j-q] or [raven]
re.findall("[x-z]", text)     # equivalent to [xyz]

In [ ]:
# \ - Signals a special sequence such as an escape character, e.g. "\d"
# The r at the beginning of the string says to treat the string as a raw string
re.findall(r"\d", text2)

In [ ]:
# . - Any character (except newline character)
re.findall(".apping", text)

In [ ]:
# ^ - Starts with
re.findall("^Th", text2)

In [ ]:
# $ - ends with
re.findall("ou.$", text2)

In [ ]:
# * - 0 or more occurrences
re.findall(".ap*ing", text)

In [ ]:
# + - 1 or more occurrences
re.findall(".ap+ing", text)

In [ ]:
# ? - 0 or 1 occurrences
re.findall("ap?ing", text)

In [ ]:
# {} - exact number of occurrences, e.g. {2}
re.findall("ap{2}ing", text)

In [ ]:
# | - either or
re.findall("[n|r]apping", text)

## Sets
1. [abc] - matches a, b or c
2. [a-n] - matches any letter between lowercase a and lowercase n
3. [^abc] - matches anything except a, b or c
4. [0-9][0-9] - matches any two digit number
5. [a-zA-Z] - match any alphabetical character
6. [+] - match any one character

## Special Sequences
1. \A - Returns a match if the specified characters are at the beginning of the string
2. \b - Returns a match where the specified characters are at the beginning or at the end of a word
3. \B - Returns a match where the specified characters are present, but NOT at the beginning (or at the end) of a word
4. \d - Returns a match where the string contains digits (numbers from 0-9)
5. \D - Returns a match where the string DOES NOT contain digits
6. \s - Returns a match where the string contains a white space character
7. \S - Returns a match where the string DOES NOT contain a white space character
8. \w - Returns a match where the string contains any word characters (including digits and underscore)
9. \W - Returns a match where the string DOES NOT contain any word characters
10. \Z - Returns a match if the specified characters are at the end of the string

## Regex Basics — Functions
1. findall
2. search
3. split
4. sub
5. fullmatch

## Cleaning Messy Text Data

In [ ]:
data = Table().with_columns(
    "Raw Text", ["<div>Hello!</div>", "   Waded   ", "Email: waded@example.com", "Phone: (406) 994-1234"]
)
data

In [ ]:
def text_length(x):
    return len(x)

In [ ]:
data = data.with_column("Raw Length", data.apply(text_length, "Raw Text"))
data

In [ ]:
def clean_text(text):
    """ Remove HTML tags and trim whitespace """
    text = re.sub(r"<.*?>", "", text)    # Remove HTML
    text = text.strip()                  # Trim whitespace
    return text

In [ ]:
data = data.with_column("Cleaned Text", data.apply(clean_text, "Raw Text"))
data.show()

In [ ]:
data = data.with_column("Cleaned Length", data.apply(text_length, "Cleaned Text"))
data

## Pattern Matching for Validation
Use regex to validate formats such as email addresses.

In [ ]:
emails = Table().with_column("Email", ["satya@microsoft.com", "bad-email@", "waded.cruzado@cs.montana.edu"])
emails

In [ ]:
def is_valid_email(email):
    """Return true if e-mail address is valid"""
    pattern = r"^[\w.-]+@[\w.-]+\.\w+$"
    return bool(re.fullmatch(pattern, email))

In [ ]:
emails = emails.with_column("Valid?", emails.apply(is_valid_email, "Email"))
emails

## Active Learning

In [ ]:
# Question 1 - Explain the solution below
# Add a column that states whether each entry is a valid MM/DD/YYYY
# Assume the months are 0-19, each month has 0-29 days and years range from 2000-2099
dates = Table().with_column("Legal Date?", make_array("7/01/2025", "8/12/2025", "12/1/2025", "hello", "0/30/2099"))
dates

In [ ]:
def is_valid_date(candidate):
    """ Return true if date is valid """
    pattern = r"^[01]?\d/[0-2]?\d/20\d{2}$" 
    return bool(re.fullmatch(pattern, candidate))

In [ ]:
dates = dates.with_column("Valid?", dates.apply(is_valid_date, "Legal Date?"))
dates

In [ ]:
# Question 2 - Explain the solution below
# Add a column that states whether each phone number is in this format (ddd)ddd-ddd
phone_numbers = Table().with_column("Legal Phone?", make_array("(123)456-7890", "123.456-7890", "(123)-456-7890", "(123)456-789"))
phone_numbers

In [ ]:
def is_valid_phone(candidate):
    """ Return true if phone number is in this format (ddd)ddd-dddd """
    pattern = r"^\(\d{3}\)\d{3}-\d{4}$"
    return bool(re.fullmatch(pattern, candidate))

In [ ]:
phone_numbers = phone_numbers.with_column("Valid?", phone_numbers.apply(is_valid_phone, "Legal Phone?"))
phone_numbers

In [ ]:
# Question 3 - Explain the solution below
# Convert phone numbers in format ddd-ddd-dddd to (ddd)ddd-dddd

In [ ]:
text = "Your phone is 123-456-7890 and mine is 098-765-4321!"
pattern = r"(\d{3})-(\d{3})-(\d{4})"    # The parenthese indicate capture groups
replacement = r"(\1)\2-\3"               # \1 is capture group 1
result = re.sub(pattern, replacement, text)
result